In [ ]:
from pathlib import Path

import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from misc import model_config

In [2]:
main_model_config = (
    model_config.query("main")
    .drop(columns="main")
    .rename(columns={k: f"model_{k}" for k in model_config.columns})
)

new_name = {
    "powermoe": "PowerMoE",
    "llamamoe": "LLaMA-MoE-v1",
    "olmoe": "OLMoE",
    "switch": "SwitchTransformers",
    "llamamoe2": "LLaMA-MoE-v2",
    "jetmoe": "JetMoE",
    "openmoe": "OpenMoE",
    "minicpm": "MiniCPM-MoE",
    "qwen": "Qwen1.5-MoE",
    "deepseek2": "DeepSeek-V2-Lite",
    "deepseek": "DeepSeekMoE",
    "xverse": "XVERSE-MoE",
    "qwen3": "Qwen3",
    "yuan": "Yuan2.0",
    "phi": "Phi-3.5-MoE",
    "grin": "GRIN-MoE",
    "mixtral": "Mixtral-8x7B",
    "jamba": "Jamba-Mini",
    "nllb": "NLLB-MoE",
    "qwen2": "Qwen2",
}

model_colors = {
    key: px.colors.qualitative.Dark24[i] for i, key in enumerate(main_model_config.index.values)
}

seg_lens = (4, 16, 64, 256)
seg_len_colors = {key: px.colors.qualitative.Plotly[i] for i, key in enumerate(seg_lens)}
main_model_config

model_name model_abbr model_type  \
key                                                            
powermoe                   PowerMoE-3B         PW     causal   
llamamoe             LLaMA-MoE-v1-3.5B        LL1     causal   
olmoe                 OLMoE-1B-7B-0125         OL     causal   
switch     SwitchTransformers-Base-128         ST    seq2seq   
llamamoe2            LLaMA-MoE-v2-3.8B        LL2     causal   
jetmoe                       JetMoE-8B         JT     causal   
openmoe                     OpenMoE-8B         OP     causal   
minicpm               MiniCPM-MoE-8x2B         MC     causal   
qwen                 Qwen1.5-MoE-A2.7B        QW1     causal   
deepseek2             DeepSeek-V2-Lite        DS2     causal   
deepseek                   DeepSeekMoE        DS1     causal   
xverse                XVERSE-MoE-A4.2B         XV     causal   
qwen3                    Qwen3-30B-A3B        QW3     causal   
yuan                       Yuan2.0-M32         Y2     causal   
phi                        Phi-3.5-MoE         PH     causal   
grin                          GRIN-MoE         GR     causal   
mixtral              Mixtral-8x7B-v0.1         MX     causal   
jamba                   Jamba-Mini-1.6         JB     causal   
nllb                      NLLB-MoE-54B         NL    seq2seq   
qwen2                   Qwen2-57B-A14B        QW2     causal   

           model_num_params  model_num_layers  model_num_experts  model_top_k  \
key                                                                             
powermoe               3.30                32                 40            8   
llamamoe               6.74                32                 16            4   
olmoe                  6.92                16                 64            8   
switch                 7.42                24                128            1   
llamamoe2              8.03                32                  8            2   
jetmoe                 8.52                24                  8            2   
openmoe               11.86                24                 32            2   
minicpm               13.87                40                  8            2   
qwen                  14.32                24                 60            4   
deepseek2             15.71                27                 64            6   
deepseek              16.38                28                 64            6   
xverse                25.78                28                 64            6   
qwen3                 30.53                48                128            8   
yuan                  39.94                24                 32            2   
phi                   41.87                32                 16            2   
grin                  41.87                32                 16            2   
mixtral               46.70                32                  8            2   
jamba                 51.57                32                 16            2   
nllb                  54.50                48                128            2   
qwen2                 57.41                28                 64            8   

                  model_attn  
key                           
powermoe   flash_attention_2  
llamamoe               eager  
olmoe      flash_attention_2  
switch                 eager  
llamamoe2  flash_attention_2  
jetmoe     flash_attention_2  
openmoe                eager  
minicpm    flash_attention_2  
qwen       flash_attention_2  
deepseek2  flash_attention_2  
deepseek   flash_attention_2  
xverse     flash_attention_2  
qwen3      flash_attention_2  
yuan       flash_attention_2  
phi        flash_attention_2  
grin       flash_attention_2  
mixtral    flash_attention_2  
jamba      flash_attention_2  
nllb                   eager  
qwen2      flash_attention_2

In [3]:
def make_abbr(df):
    return (
        f"{df['model_abbr']}{'d' if df['is_decoder'] else 'e'}"
        if df["model_type"] == "seq2seq"
        else df["model_abbr"]
    )

In [ ]:
root_dir = Path("../output/sch_mpq")

dfs = {
    p.stem: pd.merge(pd.read_parquet(p), main_model_config, left_on="model", right_index=True)
    for p in root_dir.glob("*.parquet")
}

for df in dfs.values():
    df["model"] = df["model"].astype(model_config.index.dtype)

dfs["m"]

model  is_decoder  dataset  seg_len   cache_m    recall     ci_lb  \
0        powermoe        True       c4        4  0.003906  0.003906  0.003906   
1        powermoe        True       c4        4  0.007812  0.007812  0.007812   
2        powermoe        True       c4        4  0.011719  0.011719  0.011719   
3        powermoe        True       c4        4  0.015625  0.015625  0.015625   
4        powermoe        True       c4        4  0.019531  0.019531  0.019531   
...           ...         ...      ...      ...       ...       ...       ...   
1149435     qwen2        True  science      256  7.982143  1.000000  1.000000   
1149436     qwen2        True  science      256  7.986607  1.000000  1.000000   
1149437     qwen2        True  science      256  7.991071  1.000000  1.000000   
1149438     qwen2        True  science      256  7.995536  1.000000  1.000000   
1149439     qwen2        True  science      256  8.000000  1.000000  1.000000   

            ci_ub      model_name model_abbr model_type  model_num_params  \
0        0.003906     PowerMoE-3B         PW     causal              3.30   
1        0.007812     PowerMoE-3B         PW     causal              3.30   
2        0.011719     PowerMoE-3B         PW     causal              3.30   
3        0.015625     PowerMoE-3B         PW     causal              3.30   
4        0.019531     PowerMoE-3B         PW     causal              3.30   
...           ...             ...        ...        ...               ...   
1149435  1.000000  Qwen2-57B-A14B        QW2     causal             57.41   
1149436  1.000000  Qwen2-57B-A14B        QW2     causal             57.41   
1149437  1.000000  Qwen2-57B-A14B        QW2     causal             57.41   
1149438  1.000000  Qwen2-57B-A14B        QW2     causal             57.41   
1149439  1.000000  Qwen2-57B-A14B        QW2     causal             57.41   

         model_num_layers  model_num_experts  model_top_k         model_attn  
0                      32                 40            8  flash_attention_2  
1                      32                 40            8  flash_attention_2  
2                      32                 40            8  flash_attention_2  
3                      32                 40            8  flash_attention_2  
4                      32                 40            8  flash_attention_2  
...                   ...                ...          ...                ...  
1149435                28                 64            8  flash_attention_2  
1149436                28                 64            8  flash_attention_2  
1149437                28                 64            8  flash_attention_2  
1149438                28                 64            8  flash_attention_2  
1149439                28                 64            8  flash_attention_2  

[1032064 rows x 16 columns]

In [ ]:
dfs["m"].query("cache_m == 2").groupby(
    ["model", "is_decoder", "seg_len"], as_index=False, observed=True
)[["recall"]].mean().pivot(
    index=["model", "is_decoder"], columns="seg_len", values="recall"
).sort_values(16, ascending=False)

seg_len                    4         16        64        256
model     is_decoder                                        
llamamoe2 True        0.999365  0.985314  0.974056  0.967488
yuan      True        0.950463  0.824813  0.785438  0.766915
powermoe  True        0.928987  0.802172  0.746407  0.720497
qwen3     True        0.916601  0.756180  0.672170  0.618575
phi       True        0.895927  0.744333  0.673407  0.635522
mixtral   True        0.882406  0.739457  0.663284  0.623013
minicpm   True        0.881495  0.731386  0.650123  0.608004
olmoe     True        0.893379  0.728658  0.653038  0.612885
grin      True        0.882910  0.726498  0.653082  0.613520
jetmoe    True        0.856773  0.708372  0.631002  0.591265
llamamoe  True        0.808427  0.670012  0.603038  0.571247
xverse    True        0.782398  0.574451  0.465025  0.411231
jamba     True        0.778895  0.569602  0.465581  0.412609
deepseek2 True        0.779334  0.567189  0.458800  0.402949
deepseek  True        0.770676  0.553158  0.441981  0.385109
qwen2     True        0.752185  0.548929  0.452862  0.409943
qwen      True        0.691359  0.453945  0.334765  0.276058
nllb      True        0.654847  0.450907  0.378642  0.319436
openmoe   True        0.651386  0.422329  0.324136  0.278711
nllb      False       0.623754  0.377235  0.287158  0.242144
switch    False       0.548829  0.269161  0.175811  0.138141
          True        0.554782  0.269115  0.167950       NaN

In [5]:
dfs["m"].query("cache_m == 2").groupby(
    ["model", "is_decoder", "seg_len"], as_index=False, observed=True
)[["ci_lb", "ci_ub"]].mean().pivot(index=["model", "is_decoder"], columns="seg_len").swaplevel(
    0, 1, axis=1
).sort_index(axis=1).sort_values((16, "ci_lb"), ascending=False)

seg_len                    4                   16                  64   \
                         ci_lb     ci_ub     ci_lb     ci_ub     ci_lb   
model     is_decoder                                                     
llamamoe2 True        0.999347  0.999384  0.985060  0.985570  0.973635   
yuan      True        0.949923  0.950992  0.823946  0.825665  0.784436   
powermoe  True        0.928480  0.929475  0.801326  0.802982  0.745301   
qwen3     True        0.915791  0.917399  0.754804  0.757526  0.670337   
phi       True        0.894849  0.896997  0.742534  0.746200  0.670998   
mixtral   True        0.881986  0.882810  0.738863  0.740028  0.662478   
minicpm   True        0.881089  0.881895  0.730869  0.731885  0.649530   
olmoe     True        0.892341  0.894402  0.726935  0.730353  0.650859   
grin      True        0.881818  0.883972  0.724701  0.728306  0.650730   
jetmoe    True        0.856381  0.857159  0.707904  0.708842  0.630402   
llamamoe  True        0.807964  0.808893  0.669590  0.670415  0.602549   
xverse    True        0.781702  0.783080  0.573442  0.575415  0.463865   
jamba     True        0.778248  0.779521  0.568676  0.570500  0.464310   
deepseek2 True        0.778595  0.780066  0.566170  0.568172  0.457592   
deepseek  True        0.769936  0.771412  0.552119  0.554156  0.440736   
qwen2     True        0.751787  0.752577  0.548623  0.549234  0.452558   
qwen      True        0.690694  0.692001  0.453094  0.454781  0.333734   
nllb      True        0.653795  0.655886  0.449319  0.452433  0.376941   
openmoe   True        0.650286  0.652438  0.420687  0.423865  0.322152   
nllb      False       0.623051  0.624438  0.375973  0.378438  0.285583   
switch    False       0.548146  0.549474  0.267957  0.270389  0.174360   
          True        0.553949  0.555587  0.267615  0.270563  0.166414   

seg_len                              256            
                         ci_ub     ci_lb     ci_ub  
model     is_decoder                                
llamamoe2 True        0.974470  0.966944  0.968033  
yuan      True        0.786430  0.765730  0.768095  
powermoe  True        0.747516  0.719176  0.721841  
qwen3     True        0.673966  0.616241  0.620939  
phi       True        0.675721  0.632623  0.638448  
mixtral   True        0.664052  0.622023  0.623975  
minicpm   True        0.650702  0.607313  0.608680  
olmoe     True        0.655240  0.610375  0.615384  
grin      True        0.655431  0.610738  0.616290  
jetmoe    True        0.631590  0.590519  0.591988  
llamamoe  True        0.603523  0.570677  0.571814  
xverse    True        0.466141  0.409956  0.412514  
jamba     True        0.466765  0.411048  0.414091  
deepseek2 True        0.459989  0.401499  0.404346  
deepseek  True        0.443187  0.383714  0.386466  
qwen2     True        0.453152  0.409600  0.410274  
qwen      True        0.335757  0.274871  0.277217  
nllb      True        0.380319  0.317626  0.321173  
openmoe   True        0.326031  0.276477  0.280866  
nllb      False       0.288626  0.240558  0.243728  
switch    False       0.177227  0.136571  0.139725  
          True        0.169403       NaN       NaN

In [6]:
dfs["m"].assign(
    ci_dist=np.maximum(
        dfs["m"]["ci_ub"] - dfs["m"]["recall"], dfs["m"]["recall"] - dfs["m"]["ci_lb"]
    )
).groupby(["model", "is_decoder", "dataset", "seg_len"], as_index=False, observed=True)[
    ["ci_dist"]
].max().pivot(index=["model", "is_decoder"], columns=["dataset", "seg_len"], values="ci_dist")

dataset                     c4                                  cc2306  \
seg_len                    4         16        64        256       4     
model     is_decoder                                                     
powermoe  True        0.000387  0.000627  0.000856  0.001150  0.000355   
llamamoe  True        0.000379  0.000376  0.000464  0.000592  0.000357   
olmoe     True        0.000826  0.001288  0.001716  0.002064  0.000769   
switch    False       0.000362  0.000982  0.001645  0.002277  0.000522   
          True        0.000492  0.001289  0.001811       NaN  0.000523   
llamamoe2 True        0.000541  0.000713  0.000786  0.000933  0.000505   
jetmoe    True        0.000289  0.000445  0.000579  0.000791  0.000314   
openmoe   True        0.000783  0.001225  0.001698  0.002010  0.000809   
minicpm   True        0.000310  0.000477  0.000608  0.000755  0.000419   
qwen      True        0.000591  0.000848  0.001106  0.001411  0.000631   
deepseek2 True        0.000679  0.001065  0.001379  0.001844  0.000658   
deepseek  True        0.000668  0.001133  0.001381  0.001796  0.000772   
xverse    True        0.000427  0.000602  0.000858  0.001059  0.000364   
qwen3     True        0.000726  0.001108  0.001512  0.002420  0.000728   
yuan      True        0.000480  0.000745  0.000820  0.000941  0.000489   
phi       True        0.000737  0.001159  0.001647  0.002069  0.000803   
grin      True        0.000779  0.001233  0.001654  0.002116  0.000812   
mixtral   True        0.000370  0.000612  0.000759  0.000977  0.000431   
jamba     True        0.000549  0.000783  0.001058  0.001366  0.000595   
nllb      False       0.000443  0.000812  0.001222  0.001504  0.000521   
          True        0.000765  0.001160  0.001332  0.001531  0.000578   
qwen2     True        0.000274  0.000237  0.000260  0.000322  0.000293   

dataset                                                 book            ...  \
seg_len                    16        64        256       4         16   ...   
model     is_decoder                                                    ...   
powermoe  True        0.000637  0.000871  0.001039  0.000454  0.000584  ...   
llamamoe  True        0.000367  0.000421  0.000447  0.000414  0.000281  ...   
olmoe     True        0.001345  0.001553  0.001887  0.000726  0.001247  ...   
switch    False       0.001166  0.001717  0.002184  0.000415  0.001234  ...   
          True        0.001327  0.001732       NaN  0.000524  0.001526  ...   
llamamoe2 True        0.000680  0.000720  0.000801  0.000513  0.000671  ...   
jetmoe    True        0.000398  0.000556  0.000693  0.000301  0.000321  ...   
openmoe   True        0.001271  0.001601  0.001853  0.001073  0.001704  ...   
minicpm   True        0.000697  0.000702  0.000749  0.000303  0.000367  ...   
qwen      True        0.000844  0.001172  0.001455  0.000546  0.000793  ...   
deepseek2 True        0.001092  0.001380  0.001538  0.000570  0.000749  ...   
deepseek  True        0.001123  0.001417  0.001601  0.000556  0.000817  ...   
xverse    True        0.000528  0.000744  0.000865  0.000395  0.000520  ...   
qwen3     True        0.001111  0.001523  0.002059  0.000655  0.001152  ...   
yuan      True        0.000697  0.000822  0.000949  0.000523  0.000825  ...   
phi       True        0.001173  0.001511  0.001982  0.000783  0.001040  ...   
grin      True        0.001223  0.001418  0.001966  0.000772  0.001057  ...   
mixtral   True        0.000635  0.000812  0.000971  0.000433  0.000469  ...   
jamba     True        0.000824  0.000975  0.001278  0.000555  0.000732  ...   
nllb      False       0.000896  0.001108  0.001238  0.000431  0.000890  ...   
          True        0.000974  0.001131  0.001408  0.000590  0.001138  ...   
qwen2     True        0.000254  0.000286  0.000327  0.000345  0.000241  ...   

dataset                   math                code                      \
seg_len                    64        256       4         16        64    
model     is_decoder     

In [12]:
mdf = pd.merge(
    dfs["m"]
    .groupby(["model", "is_decoder", "seg_len", "cache_m"], as_index=False, observed=True)[
        ["recall"]
    ]
    .mean(),
    main_model_config,
    left_on="model",
    right_index=True,
)

mdf

model  is_decoder  seg_len   cache_m    recall      model_name  \
0      powermoe        True        4  0.003906  0.003906     PowerMoE-3B   
1      powermoe        True        4  0.007812  0.007812     PowerMoE-3B   
2      powermoe        True        4  0.011719  0.011719     PowerMoE-3B   
3      powermoe        True        4  0.015625  0.015625     PowerMoE-3B   
4      powermoe        True        4  0.019531  0.019531     PowerMoE-3B   
...         ...         ...      ...       ...       ...             ...   
93819     qwen2        True      256  7.982143  1.000000  Qwen2-57B-A14B   
93820     qwen2        True      256  7.986607  1.000000  Qwen2-57B-A14B   
93821     qwen2        True      256  7.991071  1.000000  Qwen2-57B-A14B   
93822     qwen2        True      256  7.995536  1.000000  Qwen2-57B-A14B   
93823     qwen2        True      256  8.000000  1.000000  Qwen2-57B-A14B   

      model_abbr model_type  model_num_params  model_num_layers  \
0             PW     causal              3.30                32   
1             PW     causal              3.30                32   
2             PW     causal              3.30                32   
3             PW     causal              3.30                32   
4             PW     causal              3.30                32   
...          ...        ...               ...               ...   
93819        QW2     causal             57.41                28   
93820        QW2     causal             57.41                28   
93821        QW2     causal             57.41                28   
93822        QW2     causal             57.41                28   
93823        QW2     causal             57.41                28   

       model_num_experts  model_top_k         model_attn  
0                     40            8  flash_attention_2  
1                     40            8  flash_attention_2  
2                     40            8  flash_attention_2  
3                     40            8  flash_attention_2  
4                     40            8  flash_attention_2  
...                  ...          ...                ...  
93819                 64            8  flash_attention_2  
93820                 64            8  flash_attention_2  
93821                 64            8  flash_attention_2  
93822                 64            8  flash_attention_2  
93823                 64            8  flash_attention_2  

[93824 rows x 13 columns]

In [ ]:
srp_dir = Path("../output/srp_mpq")

rdf = pd.merge(
    pd.read_parquet(srp_dir / "mg.parquet"), main_model_config, left_on="model", right_index=True
)

sorted_model_keys = rdf.query("is_decoder and seg_len == 16").sort_values(
    "best_f1", ascending=False
)["model"]

cdf = (
    pd.merge(mdf, rdf)
    .query("cache_m.isin((0.5, 1, 1.5, 2, 2.5, 3))")
    .groupby(["seg_len", "cache_m"], as_index=False)
    .apply(lambda df: pd.Series({"corr": df["recall"].corr(df["best_f1"])}), include_groups=False)
)

cdf.pivot(index="seg_len", columns="cache_m", values="corr")

cache_m       0.5       1.0       1.5       2.0       2.5       3.0
seg_len                                                            
4        0.965829  0.979832  0.982089  0.960389  0.890650  0.750535
16       0.978689  0.995168  0.997550  0.984886  0.956964  0.923314
64       0.967460  0.990054  0.997799  0.990243  0.968081  0.936023
256      0.954106  0.983185  0.995826  0.991970  0.971122  0.936997

In [20]:
dash_level = {
    "llamamoe2": 0,
    "yuan": 0,
    "powermoe": 0,
    "qwen3": 0,
    "phi": 0,
    "olmoe": 0,
    "grin": 0,
    "mixtral": 1,
    "minicpm": 1,
    "jetmoe": 1,
    "llamamoe": 1,
    "xverse": 2,
    "jamba": 2,
    "deepseek2": 2,
    "deepseek": 2,
    "qwen2": 2,
    "nllb": 3,
    "qwen": 3,
    "openmoe": 3,
    "switch": 3,
}

dash_style = ["solid", "longdash", "dashdot", "dot"]
dash_type = {k: dash_style[v] for k, v in dash_level.items()}

In [ ]:
fig = make_subplots(
    rows=1,
    cols=len(seg_lens),
    shared_xaxes="all",
    horizontal_spacing=0.01,
    subplot_titles=[f"m={seg_len}" for seg_len in seg_lens],
)

font_size = [16, 20, 24, 28]
show_legend = True

for i, seg_len in enumerate(seg_lens):
    col = i + 1

    for j, key in enumerate(main_model_config.index.values):
        tmpdf = mdf.query(f"model == '{key}' and seg_len == {seg_len}")

        if model_config.loc[key, "type"] == "seq2seq":
            for is_decoder in (False, True):
                subdf = tmpdf.query(f"is_decoder == {is_decoder}")

                fig.add_scatter(
                    x=subdf["cache_m"],
                    y=subdf["recall"],
                    hoverinfo="skip",
                    legendgroup=key,
                    line=go.scatter.Line(color=model_colors[key], dash=dash_type[key], width=2),
                    mode="lines",
                    name=f"{new_name[key]} ({'De' if is_decoder else 'En'}coder)",
                    opacity=1 if is_decoder else 0.5,
                    showlegend=show_legend,
                    row=1,
                    col=col,
                )
        else:
            fig.add_scatter(
                x=tmpdf["cache_m"],
                y=tmpdf["recall"],
                hoverinfo="skip",
                legendgroup=key,
                line=go.scatter.Line(color=model_colors[key], dash=dash_type[key], width=2),
                mode="lines",
                name=new_name[key],
                showlegend=show_legend,
                row=1,
                col=col,
            )

        fig.update_xaxes(
            range=[0, 4],
            tickfont=go.layout.xaxis.Tickfont(size=font_size[1]),
            title=go.layout.xaxis.Title(
                font=go.layout.xaxis.title.Font(size=font_size[2]), text="ρ"
            ),
            row=1,
            col=col,
        )

        fig.update_yaxes(range=[0, 1], showticklabels=col == 1, row=1, col=col)

        if col == 1:
            fig.update_yaxes(
                tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
                title=go.layout.yaxis.Title(
                    font=go.layout.yaxis.title.Font(size=font_size[2]), text="SCH(E,m,ρ)"
                ),
                row=1,
                col=col,
            )

    show_legend = False

fig.update_annotations(font=go.layout.annotation.Font(size=font_size[3]))

fig.update_layout(
    legend=go.layout.Legend(
        font=go.layout.legend.Font(size=font_size[1]),
        itemsizing="constant",
        orientation="h",
        y=-0.15,
        yanchor="top",
    ),
    margin=go.layout.Margin(l=60, r=30, t=30, b=15),
    width=2000,
    height=600,
)

fig.write_image("./plot/msch.pdf", width=fig.layout.width, height=fig.layout.height)
fig.show()

In [18]:
ldf = pd.merge(
    dfs["l"]
    .groupby(
        ["model", "is_decoder", "layer_idx", "seg_len", "cache_m"], as_index=False, observed=True
    )[["recall"]]
    .mean(),
    main_model_config,
    left_on="model",
    right_index=True,
)

ldf

model  is_decoder  layer_idx  seg_len  cache_m    recall  \
0      powermoe        True          0        4    0.125  0.105572   
1      powermoe        True          0        4    0.250  0.200081   
2      powermoe        True          0        4    0.375  0.286259   
3      powermoe        True          0        4    0.500  0.364742   
4      powermoe        True          0        4    0.625  0.436532   
...         ...         ...        ...      ...      ...       ...   
93819     qwen2        True         27      256    7.500  0.961675   
93820     qwen2        True         27      256    7.625  0.972169   
93821     qwen2        True         27      256    7.750  0.982209   
93822     qwen2        True         27      256    7.875  0.991632   
93823     qwen2        True         27      256    8.000  1.000000   

           model_name model_abbr model_type  model_num_params  \
0         PowerMoE-3B         PW     causal              3.30   
1         PowerMoE-3B         PW     causal              3.30   
2         PowerMoE-3B         PW     causal              3.30   
3         PowerMoE-3B         PW     causal              3.30   
4         PowerMoE-3B         PW     causal              3.30   
...               ...        ...        ...               ...   
93819  Qwen2-57B-A14B        QW2     causal             57.41   
93820  Qwen2-57B-A14B        QW2     causal             57.41   
93821  Qwen2-57B-A14B        QW2     causal             57.41   
93822  Qwen2-57B-A14B        QW2     causal             57.41   
93823  Qwen2-57B-A14B        QW2     causal             57.41   

       model_num_layers  model_num_experts  model_top_k         model_attn  
0                    32                 40            8  flash_attention_2  
1                    32                 40            8  flash_attention_2  
2                    32                 40            8  flash_attention_2  
3                    32                 40            8  flash_attention_2  
4                    32                 40            8  flash_attention_2  
...                 ...                ...          ...                ...  
93819                28                 64            8  flash_attention_2  
93820                28                 64            8  flash_attention_2  
93821                28                 64            8  flash_attention_2  
93822                28                 64            8  flash_attention_2  
93823                28                 64            8  flash_attention_2  

[93824 rows x 14 columns]

In [19]:
num_cols = 10
num_rows = (len(main_model_config) - 1) // num_cols + 1

fig = make_subplots(
    rows=num_rows,
    cols=num_cols,
    shared_xaxes="all",
    shared_yaxes="all",
    horizontal_spacing=0.005,
    vertical_spacing=0.11,
    subplot_titles=sorted_model_keys.map(new_name).values,
)

font_size = [16, 16, 18, 20]
show_legend = True

for i, key in enumerate(sorted_model_keys):
    if (ldf["model"] == key).sum() == 0:
        continue

    row = i // num_cols + 1
    col = i % num_cols + 1
    num_layers = model_config.loc[key, "num_layers"]

    for seg_len in seg_lens:
        for j, cache_m in enumerate((1, 2)):
            tmpdf = ldf.query(f"model == '{key}' and seg_len == {seg_len} and cache_m == {cache_m}")

            if len(tmpdf) == 0:
                continue

            layer_idx = tmpdf["layer_idx"] + 1
            if model_config.loc[key, "type"] == "seq2seq":
                layer_idx += tmpdf["is_decoder"] * model_config.loc[key, "num_layers"] // 2

            line_name = f"SCH(E,{seg_len},{cache_m})"

            fig.add_scatter(
                x=layer_idx / num_layers,
                y=tmpdf["recall"],
                hoverinfo="skip",
                legendgroup=line_name,
                line=go.scatter.Line(color=seg_len_colors[seg_len], dash="dot" if j else "solid"),
                marker=go.scatter.Marker(size=4),
                mode="lines" if j else "lines+markers",
                name=line_name,
                opacity=0.5 if j else 1,
                showlegend=show_legend,
                row=row,
                col=col,
            )

    show_legend = False

    fig.update_xaxes(
        showticklabels=True,
        tickfont=go.layout.xaxis.Tickfont(size=font_size[1]),
        tickvals=[1 / num_layers, 0.5, 1],
        ticktext=[1, num_layers // 2, num_layers],
        row=row,
        col=col,
    )

    if row == num_rows:
        fig.update_xaxes(
            title=go.layout.xaxis.Title(
                font=go.layout.xaxis.title.Font(size=font_size[2]), standoff=1, text="Layer"
            ),
            row=row,
            col=col,
        )

    fig.update_yaxes(showticklabels=col == 1, row=row, col=col)

    if col == 1:
        fig.update_yaxes(
            tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
            title=go.layout.yaxis.Title(
                font=go.layout.yaxis.title.Font(size=font_size[2]), text="SCH(E,m,ρ)"
            ),
            row=row,
            col=col,
        )

fig.update_annotations(font=go.layout.annotation.Font(size=font_size[3]))

fig.update_layout(
    legend=go.layout.Legend(
        font=go.layout.legend.Font(size=font_size[2]), orientation="h", x=0.47, xanchor="center"
    ),
    margin=go.layout.Margin(l=60, r=15, t=30, b=15),
    width=2000,
    height=500,
)

fig.write_image("./plot/lsch.pdf", width=fig.layout.width, height=fig.layout.height)
fig.show()

In [21]:
d1mdf = mdf.assign(
    diff1=mdf.groupby(["model", "is_decoder", "seg_len"], observed=True)[["cache_m", "recall"]]
    .diff()
    .apply(lambda s: s["recall"] / s["cache_m"], axis=1)
)

d1mdf

model  is_decoder  seg_len   cache_m    recall      model_name  \
0      powermoe        True        4  0.003906  0.003906     PowerMoE-3B   
1      powermoe        True        4  0.007812  0.007812     PowerMoE-3B   
2      powermoe        True        4  0.011719  0.011719     PowerMoE-3B   
3      powermoe        True        4  0.015625  0.015625     PowerMoE-3B   
4      powermoe        True        4  0.019531  0.019531     PowerMoE-3B   
...         ...         ...      ...       ...       ...             ...   
93819     qwen2        True      256  7.982143  1.000000  Qwen2-57B-A14B   
93820     qwen2        True      256  7.986607  1.000000  Qwen2-57B-A14B   
93821     qwen2        True      256  7.991071  1.000000  Qwen2-57B-A14B   
93822     qwen2        True      256  7.995536  1.000000  Qwen2-57B-A14B   
93823     qwen2        True      256  8.000000  1.000000  Qwen2-57B-A14B   

      model_abbr model_type  model_num_params  model_num_layers  \
0             PW     causal              3.30                32   
1             PW     causal              3.30                32   
2             PW     causal              3.30                32   
3             PW     causal              3.30                32   
4             PW     causal              3.30                32   
...          ...        ...               ...               ...   
93819        QW2     causal             57.41                28   
93820        QW2     causal             57.41                28   
93821        QW2     causal             57.41                28   
93822        QW2     causal             57.41                28   
93823        QW2     causal             57.41                28   

       model_num_experts  model_top_k         model_attn  diff1  
0                     40            8  flash_attention_2    NaN  
1                     40            8  flash_attention_2    1.0  
2                     40            8  flash_attention_2    1.0  
3                     40            8  flash_attention_2    1.0  
4                     40            8  flash_attention_2    1.0  
...                  ...          ...                ...    ...  
93819                 64            8  flash_attention_2    0.0  
93820                 64            8  flash_attention_2    0.0  
93821                 64            8  flash_attention_2    0.0  
93822                 64            8  flash_attention_2    0.0  
93823                 64            8  flash_attention_2    0.0  

[93824 rows x 14 columns]

In [22]:
fig = make_subplots(
    rows=1,
    cols=len(seg_lens),
    shared_xaxes="all",
    horizontal_spacing=0.01,
    subplot_titles=[f"m={seg_len}" for seg_len in seg_lens],
)

font_size = [16, 20, 24, 28]
show_legend = True

for i, seg_len in enumerate(seg_lens):
    col = i + 1

    for j, key in enumerate(main_model_config.index.values):
        tmpdf = d1mdf.query(f"model == '{key}' and seg_len == {seg_len}")

        if model_config.loc[key, "type"] == "seq2seq":
            for is_decoder in (False, True):
                subdf = tmpdf.query(f"is_decoder == {is_decoder}")

                fig.add_scatter(
                    x=subdf["cache_m"],
                    y=subdf["diff1"],
                    hoverinfo="skip",
                    legendgroup=key,
                    line=go.scatter.Line(color=model_colors[key], dash=dash_type[key], width=2),
                    mode="lines",
                    name=f"{new_name[key]} ({'De' if is_decoder else 'En'}coder)",
                    opacity=1 if is_decoder else 0.5,
                    showlegend=show_legend,
                    row=1,
                    col=col,
                )
        else:
            fig.add_scatter(
                x=tmpdf["cache_m"],
                y=tmpdf["diff1"],
                hoverinfo="skip",
                legendgroup=key,
                line=go.scatter.Line(color=model_colors[key], dash=dash_type[key], width=2),
                mode="lines",
                name=new_name[key],
                showlegend=show_legend,
                row=1,
                col=col,
            )

        fig.update_xaxes(
            range=[0, 4],
            tickfont=go.layout.xaxis.Tickfont(size=font_size[1]),
            title=go.layout.xaxis.Title(
                font=go.layout.xaxis.title.Font(size=font_size[2]), text="ρ"
            ),
            row=1,
            col=col,
        )

        fig.update_yaxes(range=[0, 1], showticklabels=col == 1, row=1, col=col)

        if col == 1:
            fig.update_yaxes(
                tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
                title=go.layout.yaxis.Title(
                    font=go.layout.yaxis.title.Font(size=font_size[2]), text="dSCH(E,m,ρ)/dρ"
                ),
                row=1,
                col=col,
            )

    show_legend = False

fig.update_annotations(font=go.layout.annotation.Font(size=font_size[3]))

fig.update_layout(
    legend=go.layout.Legend(
        font=go.layout.legend.Font(size=font_size[1]),
        itemsizing="constant",
        orientation="h",
        y=-0.15,
        yanchor="top",
    ),
    margin=go.layout.Margin(l=60, r=30, t=30, b=15),
    width=2000,
    height=600,
)

fig.write_image("./plot/mschd1.pdf", width=fig.layout.width, height=fig.layout.height)
fig.show()

In [23]:
d2mdf = d1mdf.assign(
    diff2=d1mdf.groupby(["model", "is_decoder", "seg_len"], observed=True)[["cache_m", "diff1"]]
    .diff()
    .apply(lambda s: s["diff1"] / s["cache_m"], axis=1)
)

d2mdf

model  is_decoder  seg_len   cache_m    recall      model_name  \
0      powermoe        True        4  0.003906  0.003906     PowerMoE-3B   
1      powermoe        True        4  0.007812  0.007812     PowerMoE-3B   
2      powermoe        True        4  0.011719  0.011719     PowerMoE-3B   
3      powermoe        True        4  0.015625  0.015625     PowerMoE-3B   
4      powermoe        True        4  0.019531  0.019531     PowerMoE-3B   
...         ...         ...      ...       ...       ...             ...   
93819     qwen2        True      256  7.982143  1.000000  Qwen2-57B-A14B   
93820     qwen2        True      256  7.986607  1.000000  Qwen2-57B-A14B   
93821     qwen2        True      256  7.991071  1.000000  Qwen2-57B-A14B   
93822     qwen2        True      256  7.995536  1.000000  Qwen2-57B-A14B   
93823     qwen2        True      256  8.000000  1.000000  Qwen2-57B-A14B   

      model_abbr model_type  model_num_params  model_num_layers  \
0             PW     causal              3.30                32   
1             PW     causal              3.30                32   
2             PW     causal              3.30                32   
3             PW     causal              3.30                32   
4             PW     causal              3.30                32   
...          ...        ...               ...               ...   
93819        QW2     causal             57.41                28   
93820        QW2     causal             57.41                28   
93821        QW2     causal             57.41                28   
93822        QW2     causal             57.41                28   
93823        QW2     causal             57.41                28   

       model_num_experts  model_top_k         model_attn  diff1  diff2  
0                     40            8  flash_attention_2    NaN    NaN  
1                     40            8  flash_attention_2    1.0    NaN  
2                     40            8  flash_attention_2    1.0    0.0  
3                     40            8  flash_attention_2    1.0    0.0  
4                     40            8  flash_attention_2    1.0    0.0  
...                  ...          ...                ...    ...    ...  
93819                 64            8  flash_attention_2    0.0    0.0  
93820                 64            8  flash_attention_2    0.0    0.0  
93821                 64            8  flash_attention_2    0.0    0.0  
93822                 64            8  flash_attention_2    0.0    0.0  
93823                 64            8  flash_attention_2    0.0    0.0  

[93824 rows x 15 columns]

In [24]:
fig = make_subplots(
    rows=1,
    cols=len(seg_lens),
    shared_xaxes="all",
    horizontal_spacing=0.01,
    subplot_titles=[f"m={seg_len}" for seg_len in seg_lens],
)

font_size = [16, 20, 24, 28]
show_legend = True

for i, seg_len in enumerate(seg_lens):
    col = i + 1

    for j, key in enumerate(main_model_config.index.values):
        tmpdf = d2mdf.query(f"model == '{key}' and seg_len == {seg_len}")

        if model_config.loc[key, "type"] == "seq2seq":
            for is_decoder in (False, True):
                subdf = tmpdf.query(f"is_decoder == {is_decoder}")

                fig.add_scatter(
                    x=subdf["cache_m"],
                    y=subdf["diff2"],
                    hoverinfo="skip",
                    legendgroup=key,
                    line=go.scatter.Line(color=model_colors[key], dash=dash_type[key], width=2),
                    mode="lines",
                    name=f"{new_name[key]} ({'De' if is_decoder else 'En'}coder)",
                    opacity=1 if is_decoder else 0.5,
                    showlegend=show_legend,
                    row=1,
                    col=col,
                )
        else:
            fig.add_scatter(
                x=tmpdf["cache_m"],
                y=tmpdf["diff2"],
                hoverinfo="skip",
                legendgroup=key,
                line=go.scatter.Line(color=model_colors[key], dash=dash_type[key], width=2),
                mode="lines",
                name=new_name[key],
                showlegend=show_legend,
                row=1,
                col=col,
            )

        fig.update_xaxes(
            range=[0, 4],
            tickfont=go.layout.xaxis.Tickfont(size=font_size[1]),
            title=go.layout.xaxis.Title(
                font=go.layout.xaxis.title.Font(size=font_size[2]), text="ρ"
            ),
            row=1,
            col=col,
        )

        if col == 1:
            fig.update_yaxes(
                tickfont=go.layout.yaxis.Tickfont(size=font_size[1]),
                title=go.layout.yaxis.Title(
                    font=go.layout.yaxis.title.Font(size=font_size[2]), text="d^2SCH(E,m,ρ)/dρ^2"
                ),
                row=1,
                col=col,
            )

    show_legend = False

fig.update_annotations(font=go.layout.annotation.Font(size=font_size[3]))

fig.update_layout(
    legend=go.layout.Legend(
        font=go.layout.legend.Font(size=font_size[1]),
        itemsizing="constant",
        orientation="h",
        y=-0.15,
        yanchor="top",
    ),
    margin=go.layout.Margin(l=60, r=30, t=30, b=15),
    width=2000,
    height=600,
)

fig.write_image("./plot/mschd2.pdf", width=fig.layout.width, height=fig.layout.height)
fig.show()